# Project Proposal - Data Preparation and Exploration
<br>Group: Group 11 - Alex Fung, Patrick Osborne
<br>Dataset: Twitter US Airline Sentiment
<br>Dataset link: https://www.kaggle.com/crowdflower/twitter-airline-sentiment



## Data Preparation

### Load the data

In [1]:
import pandas as pd
pd.options.display.max_colwidth = None

It is important that we read the Tweets.csv with 'utf-8' encoding, so that we can extract the emojis properly

In [2]:
df_tweets = pd.read_csv("../data/Tweets.csv", encoding='utf-8')
df_tweets.head()

tweet_id airline_sentiment  airline_sentiment_confidence  \
0  570306133677760513           neutral                        1.0000   
1  570301130888122368          positive                        0.3486   
2  570301083672813571           neutral                        0.6837   
3  570301031407624196          negative                        1.0000   
4  570300817074462722          negative                        1.0000   

  negativereason  negativereason_confidence         airline  \
0            NaN                        NaN  Virgin America   
1            NaN                     0.0000  Virgin America   
2            NaN                        NaN  Virgin America   
3     Bad Flight                     0.7033  Virgin America   
4     Can't Tell                     1.0000  Virgin America   

  airline_sentiment_gold        name negativereason_gold  retweet_count  \
0                    NaN     cairdin                 NaN              0   
1                    NaN    jnardino                 NaN              0   
2                    NaN  yvonnalynn                 NaN              0   
3                    NaN    jnardino                 NaN              0   
4                    NaN    jnardino                 NaN              0   

                                                                                                                             text  \
0                                                                                             @VirginAmerica What @dhepburn said.   
1                                                        @VirginAmerica plus you've added commercials to the experience... tacky.   
2                                                         @VirginAmerica I didn't today... Must mean I need to take another trip!   
3  @VirginAmerica it's really aggressive to blast obnoxious "entertainment" in your guests' faces &amp; they have little recourse   
4                                                                         @VirginAmerica and it's a really big bad thing about it   

  tweet_coord              tweet_created tweet_location  \
0         NaN  2015-02-24 11:35:52 -0800            NaN   
1         NaN  2015-02-24 11:15:59 -0800            NaN   
2         NaN  2015-02-24 11:15:48 -0800      Lets Play   
3         NaN  2015-02-24 11:15:36 -0800            NaN   
4         NaN  2015-02-24 11:14:45 -0800            NaN   

                user_timezone  
0  Eastern Time (US & Canada)  
1  Pacific Time (US & Canada)  
2  Central Time (US & Canada)  
3  Pacific Time (US & Canada)  
4  Pacific Time (US & Canada)

In [3]:
df_tweets.shape

(14640, 15)

### Check for Nulls

There are no nulls amongst the columns airline_sentiment and text, which is good

In [4]:
df_tweets['airline_sentiment'].isnull().sum()

0

In [5]:
df_tweets['text'].isnull().sum()

0

Column 'negativereason' has a few missing nulls, but they are null only if 'airline_sentiment' is positive or neutral.

In [6]:
df_tweets['negativereason'].isnull().sum()

5462

In [7]:
df_tweets['airline_sentiment'].loc[df_tweets['negativereason'].isnull()].unique()

array(['neutral', 'positive'], dtype=object)

## Cleaning Data

### 1. Remove not useful columns
Looking at the dataframe above, we can see some columns will likely not be useful for our purposes of sentiment analysis, such timezones, number of retweets, etc. 

In [8]:
df_tweets = df_tweets[
    ['tweet_id', 'airline_sentiment', 'airline_sentiment_confidence', 'negativereason', 'negativereason_confidence', 'airline', 'text']
]
df_tweets.head()

tweet_id airline_sentiment  airline_sentiment_confidence  \
0  570306133677760513           neutral                        1.0000   
1  570301130888122368          positive                        0.3486   
2  570301083672813571           neutral                        0.6837   
3  570301031407624196          negative                        1.0000   
4  570300817074462722          negative                        1.0000   

  negativereason  negativereason_confidence         airline  \
0            NaN                        NaN  Virgin America   
1            NaN                     0.0000  Virgin America   
2            NaN                        NaN  Virgin America   
3     Bad Flight                     0.7033  Virgin America   
4     Can't Tell                     1.0000  Virgin America   

                                                                                                                             text  
0                                                                                             @VirginAmerica What @dhepburn said.  
1                                                        @VirginAmerica plus you've added commercials to the experience... tacky.  
2                                                         @VirginAmerica I didn't today... Must mean I need to take another trip!  
3  @VirginAmerica it's really aggressive to blast obnoxious "entertainment" in your guests' faces &amp; they have little recourse  
4                                                                         @VirginAmerica and it's a really big bad thing about it

### 2.Create new column 'text_cleaned'
We create a column 'text_cleaned' that will contain the cleaned up version of 'text' column 

In [9]:
df_tweets['text_cleaned'] = df_tweets['text']

### 3. Remove HTML encoding
The text has not been cleaned, as there is some HTML encoding left in the text, such as "&/amp;". We will use BeautifulSoup and lxml package to remove the HTML encoding from the text.

#### Sanity Check

In [10]:
from bs4 import BeautifulSoup

#Example of what BeautifulSoup with lxml package does 
#you may need to install lxml by 'pip install lxml' for this to work, then restart kernel
example1 = BeautifulSoup('Disappointed,UNITED did NOT feed small CHILDREN on a 5 &amp; half hour flight', 'lxml')
print(example1.get_text())

Disappointed,UNITED did NOT feed small CHILDREN on a 5 & half hour flight


#### Remove HTML Encoding from text

In [11]:
df_tweets['text_cleaned'] = df_tweets['text_cleaned'].apply(lambda text: BeautifulSoup(text, 'lxml').get_text())
df_tweets['text_cleaned']

0                                                                                                                           @VirginAmerica What @dhepburn said.
1                                                                                      @VirginAmerica plus you've added commercials to the experience... tacky.
2                                                                                       @VirginAmerica I didn't today... Must mean I need to take another trip!
3                                    @VirginAmerica it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse
4                                                                                                       @VirginAmerica and it's a really big bad thing about it
                                                                                  ...                                                                          
14635                                   

### 4. Remove retweets
Retweets are denoted in 'text' column as 'RT @another_user another_user's tweet'. We should remove retweets because we need to analyze the tweets of the users, not the retweets. In this situation, retweets  provide no real value to our text exploration analysis as normally the users retweet to the airlines, so the retweets are based off the tweets from the specified airlines' Twitter PR, which are likely going to be either of neutral or positive sentiment. Removing such retweets will hopefully remove any noise that will prevent the models from classifying sentiment.

In addition to removing retweets first, we will remove any remaining mentions afterwards.

#### Sanity Check

In [12]:
regex_to_replace= r'RT \@.*'
replace_value= ''

In [13]:
import re
example1 = 'Awesome! RT @VirginAmerica: Watch nominated films at 35,000 feet. #MeetTheFleet #Oscars http://t.co/DnStITRzWy'
example1 = re.sub(regex_to_replace, replace_value, example1)
example1

'Awesome! '

#### Remove retweets from text

In [14]:
df_tweets['text_cleaned'] = df_tweets['text_cleaned'].replace(to_replace=regex_to_replace, value=replace_value, regex=True)
df_tweets['text_cleaned']

0                                                                                                                           @VirginAmerica What @dhepburn said.
1                                                                                      @VirginAmerica plus you've added commercials to the experience... tacky.
2                                                                                       @VirginAmerica I didn't today... Must mean I need to take another trip!
3                                    @VirginAmerica it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse
4                                                                                                       @VirginAmerica and it's a really big bad thing about it
                                                                                  ...                                                                          
14635                                   

### 5. Remove mentions
Sometimes, users use mentions (for example, tweet mentions include @VirginAirlines, @JetBlue, etc., in other words, the airlines' handle). They normally appear in the beginning of the users' tweets.

#### Sanity Check

In [15]:
regex_to_replace = r'\@[\w\d]*'
replace_value= ''

In [16]:
import re
example1 = '@VirginAmerica Thank you for the follow'
example1 = re.sub(regex_to_replace, replace_value, example1)
example1

' Thank you for the follow'

#### Remove mentions from text

In [17]:
df_tweets['text_cleaned'] = df_tweets['text_cleaned'].replace(to_replace=regex_to_replace, value=replace_value, regex=True)
df_tweets['text_cleaned']

0                                                                                                                                       What  said.
1                                                                                         plus you've added commercials to the experience... tacky.
2                                                                                          I didn't today... Must mean I need to take another trip!
3                                       it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse
4                                                                                                          and it's a really big bad thing about it
                                                                            ...                                                                    
14635                                                                                            thank you we go

### 6. Remove HTTP links
Should the user attach http links, we need to remove HTTP links from the text, since they provide no real value to our sentiment analysis as well. From what we can see in the data, they are mostly links to articles.

#### Sanity Check

In [18]:
regex_to_replace = r'https*://[^\s]*'
replace_value = ''

In [19]:
import re
example1 = '@VirginAmerica when are you putting some great deals from PDX to LAS or from LAS to PDX show me your love! http://t.co/enIQg0buzj'
example1 = re.sub(regex_to_replace, replace_value, example1)
example1

'@VirginAmerica when are you putting some great deals from PDX to LAS or from LAS to PDX show me your love! '

#### Removing HTTP Links from text

In [20]:
df_tweets['text_cleaned'] = df_tweets['text_cleaned'].replace(to_replace=regex_to_replace, value=replace_value, regex=True)
df_tweets['text_cleaned']

0                                                                                                                                       What  said.
1                                                                                         plus you've added commercials to the experience... tacky.
2                                                                                          I didn't today... Must mean I need to take another trip!
3                                       it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse
4                                                                                                          and it's a really big bad thing about it
                                                                            ...                                                                    
14635                                                                                            thank you we go

### 7. Extract Emojis and Emoticons
Rather than removing emojis and emoticons, emojis and emoticons can be seen as an integral part of the Internet language. Therefore, we should extract emojis and emoticons from the text if they exist, as they may be good features for sentiment analysis for "Internet"-speak.

Emojis are special characters which are shown as actual visual images, whereas emoticons are keyboard characters arranged in a certain format so that it represents a human-like facial expression.

We will use a third-party Python library called 'emot', which provides the ability to recognize and extract both emojis and emoticons. Github can be found here: https://github.com/NeelShah18/emot


#### Sanity Check

In [21]:
#Sanity check
import emot
text = "I love python 👨 :-)"
print(emot.emoji(text))
print(emot.emoticons(text))

{'value': ['👨'], 'mean': [':man:'], 'location': [[14, 14]], 'flag': True}
{'value': [':-)'], 'location': [[16, 19]], 'mean': ['Happy face smiley'], 'flag': True}


In [22]:
df_example1 = df_tweets.loc[df_tweets['tweet_id'] == 569198104806699008]
print(df_example1['text_cleaned'].to_string(index=False))
print(emot.emoji(df_example1['text_cleaned'].to_string(index=False)))
print(emot.emoticons(df_example1['text_cleaned'].to_string(index=False)))

  hahaha 😂 YOU GUYS ARE AMAZING. I LOVE YOU GUYS!!!💗
{'value': ['😂', '💗'], 'mean': [':face_with_tears_of_joy:', ':growing_heart:'], 'location': [[9, 9], [51, 51]], 'flag': True}
{'value': [], 'location': [], 'mean': [], 'flag': False}


In [23]:
df_example2 = df_tweets.loc[df_tweets['tweet_id'] == 568890074164809728]
print(df_example2['text_cleaned'].to_string(index=False))
print(emot.emoji(df_example2['text_cleaned'].to_string(index=False)))
print(emot.emoticons(df_example2['text_cleaned'].to_string(index=False)))

  we have a hot female pilot! Sweet! DCA to SFO! :-)
{'value': [], 'mean': [], 'location': [], 'flag': False}
{'value': [':-)'], 'location': [[49, 52]], 'mean': ['Happy face smiley'], 'flag': True}


#### Extracing Emojis and Emoticons from text

In [24]:
#this function will remove any emojis 
#accepts the following parameters: 
#(1) text_cleaned: roughly cleaned text in String to parse through and remove emojis
#(2) emojis_flag: boolean created by emot.emoji(...), can be accessed by calling 'flag' key in dictionary (for more information see above)
#(3) emojis: emojis object created by emot.emoji(...), can be accessed by calling 'value' key in dictionary (for more information see above)

#returns the cleaned up text without emojis

def remove_emojis(text_cleaned, emojis_flag, emojis):
    text_cleaned_no_emojis = text_cleaned
    
    #print('text_cleaned @ remove_emojis: ' + text_cleaned)
    #print('emojis_flag: ' + str(emojis_flag))
    #print('emojis: ' + str(emojis))
    
    
    #if flag is True, that means there are emojis, and we need to remove them
    if emojis_flag:
        for i in emojis:
            
            #rather than use location, we will match by String and see if we can remove it, because I'm lazy af lol
            #print(str(i))
            text_cleaned_no_emojis = text_cleaned_no_emojis.replace(i, '')
            
        if text_cleaned_no_emojis == text_cleaned:
            print('Uh...Houston, we have a problem...for the following text: ' + text_cleaned + ', for row: ' + str(i))
            print('The following emojis were not removed: ' + str(emojis))
        
    print('resulting text_cleaned_no_emojis: ' + text_cleaned_no_emojis)
    return text_cleaned_no_emojis  


In [25]:
#Testing the remove_emojis function
#df_example_remove_emojis = df_tweets_2.loc[df_tweets_2['tweet_id'] == 569198104806699008]
#print(df_example_remove_emojis['text_cleaned'].to_string(index=False))
#print(type(df_example_remove_emojis['emojis'].item()))
#print(df_example_remove_emojis['emojis'].item())
#print(df_example_remove_emojis['emojis'].item())

#text_remove_emojis = remove_emojis(df_example_remove_emojis['text_cleaned'].to_string(index=False), 
#                    df_example_remove_emojis['emojis_flag'].bool(), 
#                    df_example_remove_emojis['emojis'].item()
#                   )
#print(text_remove_emojis)

In [26]:
#this function will remove any emoticons 
#accepts the following parameters: 
#(1) text_cleaned: roughly cleaned text in String to parse through and remove emoticons
#(2) emoticons_flag: boolean created by emot.emoticons(...), can be accessed by calling 'flag' key in dictionary (for more information see above)
#(3) emoticons: emojis object created by emot.emoticons(...), can be accessed by calling 'value' key in dictionary (for more information see above)

#returns the cleaned up text without emoticons

def remove_emoticons(text_cleaned, emoticons_flag, emoticons):
    text_cleaned_no_emoticons = text_cleaned
    
    #print('text_cleaned @ remove_emoticons: ' + text_cleaned)
    #print('emoticons_flag: ' + str(emoticons_flag))
    #print('emoticons: ' + str(emoticons))
    
    #if flag is True, that means there are emoticons, and we need to remove them
    if emoticons_flag:
        for i in emoticons:
            
            #rather than use location, we will match by String and see if we can remove it, because I'm lazy af lol
            #print(str(i))
            text_cleaned_no_emoticons = text_cleaned_no_emoticons.replace(i, '')
            
        if text_cleaned_no_emoticons == text_cleaned:
            print('Uh...Houston, we have a problem...for the following text: ' + text_cleaned + ', for row: ' + str(i))
            print('The following emojis were not removed: ' + str(emoticons))
        
    print('resulting text_cleaned_no_emoticons: ' + text_cleaned_no_emoticons)
    return text_cleaned_no_emoticons  

In [27]:
#testing the remove_emoticons function
#df_example_remove_emoticons = df_tweets_2.loc[df_tweets_2['tweet_id'] == 568890074164809728]
#print(df_example_remove_emoticons['text_cleaned'].to_string(index=False))
#print(type(df_example_remove_emoticons['emoticons'].item()))
#print(df_example_remove_emoticons['emoticons'].item())
#print(df_example_remove_emoticons['emoticons'].item())

#text_remove_emmoticons = remove_emoticons(df_example_remove_emoticons['text_cleaned'].to_string(index=False), 
#                    df_example_remove_emoticons['emoticons_flag'].bool(), 
#                    df_example_remove_emoticons['emoticons'].item()
#                   )
#print(text_remove_emmoticons)

In [28]:
#When using emot.emoticons, the output when flag=False is inconsistent, it either is 
#(a) {'value': [], 'mean': [], 'location': [], 'flag': False}, or 
#(b) {'flag': False}

#df_example_not_working = df_tweets.loc[df_tweets['tweet_id'] == 570301130888122368]
#text_example_not_working = df_example_not_working['text_cleaned'].to_string(index=False)
#print(emot.emoji(text_example_not_working)['flag'])
#print(emot.emoticons(text_example_not_working)[0]['flag'])

In [29]:
#this function will extract any emojis into a separate 'emojis' column,
#while also removing said emojis from column: 'text_cleaned' 
#to form a new column: 'text_cleaned_without_emojis_emoticons'

#returns dataframe with the aforementioned new columns

import emot

#in 'emojis_emoticons' column, it will hold the emot.emoji return dictionary (see above for examples)
def extract_emojis(df_tweets):
    df_tweets_2 = df_tweets
    df_tweets_2['emojis_flag'] = ''
    df_tweets_2['emojis'] = ''
    df_tweets_2['emoticons_flag'] = ''
    df_tweets_2['emoticons'] = ''
        
    #easier to just write out code to loop through dataframe
    for i, row in df_tweets_2.iterrows():
        #print(i)
        #print(row)
        text_cleaned = df_tweets_2.at[i, 'text_cleaned']
        emojis = emot.emoji(text_cleaned)
        emoticons = emot.emoticons(text_cleaned)
        #print('EMOJIS: ' + str(emojis))
        #print('EMOTICONS: ' + str(emoticons))
        
        ##When using emot.emoticons, the output when flag=False is inconsistent, it either is 
        #(a) {'value': [], 'mean': [], 'location': [], 'flag': False}, or 
        #(b) {'flag': False}
        
        #Therefore we have a bunch of try-except the aforementioned exception that will be raised, and set the values manually
        try: 
            df_tweets_2.at[i, 'emojis_flag'] = emojis['flag']
        except:
            print('Unable to grab emojis flag at row number: ' + str(i))
            df_tweets_2.at[i, 'emojis_flag'] = False
            
        try: 
             df_tweets_2.at[i, 'emojis'] = emojis['value']
        except: 
            print('Unable to grab emojis value at row number: ' + str(i))
            df_tweets_2.at[i, 'emojis'] = []
            
        try: 
            df_tweets_2.at[i, 'emoticons_flag'] = emoticons['flag']
        except: 
            print('Unable to grab emoticons flag at row number: ' + str(i))
            df_tweets_2.at[i, 'emoticons_flag'] = False
            
            
        try: 
            df_tweets_2.at[i, 'emoticons'] = emoticons['value']
        except: 
            print('Unable to grab emoticons value at row number: ' + str(i))
            df_tweets_2.at[i, 'emoticons'] = []
    
        #afterwards, we need to remove emojis and emoticons from the
        df_tweets_2.at[i, 'text_cleaned_without_emojis_emoticons'] = remove_emojis(
            text_cleaned,
            df_tweets_2.at[i, 'emojis_flag'],
            df_tweets_2.at[i, 'emojis']
        )
        
        df_tweets_2.at[i, 'text_cleaned_without_emojis_emoticons'] = remove_emoticons(
            df_tweets_2.at[i, 'text_cleaned_without_emojis_emoticons'],
            df_tweets_2.at[i, 'emoticons_flag'],
            df_tweets_2.at[i, 'emoticons']
        )
        
    return df_tweets_2

In [30]:
#df_tweets['text_cleaned'] = df_tweets['text_cleaned'].apply(lambda text: BeautifulSoup(text, 'lxml').get_text())
#df_tweets['text_cleaned']
df_tweets = extract_emojis(df_tweets)
#df_tweets.head()

resulting text_cleaned_no_emojis:  What  said.
resulting text_cleaned_no_emoticons:  What  said.
Unable to grab emoticons flag at row number: 1
Unable to grab emoticons value at row number: 1
resulting text_cleaned_no_emojis:  plus you've added commercials to the experience... tacky.
resulting text_cleaned_no_emoticons:  plus you've added commercials to the experience... tacky.
resulting text_cleaned_no_emojis:  I didn't today... Must mean I need to take another trip!
resulting text_cleaned_no_emoticons:  I didn't today... Must mean I need to take another trip!
resulting text_cleaned_no_emojis:  it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse
resulting text_cleaned_no_emoticons:  it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse
resulting text_cleaned_no_emojis:  and it's a really big bad thing about it
resulting text_cleaned_no_emoticons:  and it's a really big bad thi

Unable to grab emoticons flag at row number: 259
Unable to grab emoticons value at row number: 259
resulting text_cleaned_no_emojis:  requested window seat and confirmed window but got stuck in middle seat. Not a good way to treat silver member
resulting text_cleaned_no_emoticons:  requested window seat and confirmed window but got stuck in middle seat. Not a good way to treat silver member
resulting text_cleaned_no_emojis:  Grand Budapest Hotel #OscarsCountdown
resulting text_cleaned_no_emoticons:  Grand Budapest Hotel #OscarsCountdown
resulting text_cleaned_no_emojis:  This is what you missed . Next trip to the 407.
resulting text_cleaned_no_emoticons:  This is what you missed . Next trip to the 407.
resulting text_cleaned_no_emojis:  #wtf I paid for direct flight on purpose not to have to stop for fuel exhausted frequent flier and nothing for inconvenience!
resulting text_cleaned_no_emoticons:  #wtf I paid for direct flight on purpose not to have to stop for fuel exhausted frequent 

resulting text_cleaned_no_emojis:  missed my flight. How does standby work?
resulting text_cleaned_no_emoticons:  missed my flight. How does standby work?
resulting text_cleaned_no_emojis: . They were very understanding and helped me out.  Thx! #Comps
resulting text_cleaned_no_emoticons: . They were very understanding and helped me out.  Thx! #Comps
resulting text_cleaned_no_emojis:  brought it all the way across the country today I see 
resulting text_cleaned_no_emoticons:  brought it all the way across the country today I see 
resulting text_cleaned_no_emojis:  thank you! I absolutely will 
resulting text_cleaned_no_emoticons:  thank you! I absolutely will 
Unable to grab emoticons flag at row number: 314
Unable to grab emoticons value at row number: 314
resulting text_cleaned_no_emojis:  Looks like a broken link for your assets 
resulting text_cleaned_no_emoticons:  Looks like a broken link for your assets 
Unable to grab emoticons flag at row number: 315
Unable to grab emoticons va

resulting text_cleaned_no_emojis:  YES FYI  MY BFF
resulting text_cleaned_no_emoticons:  YES FYI  MY BFF
resulting text_cleaned_no_emojis:  another perfect flight.   How come on your planes,  the sun visors can stay down?  Other carriers make you raise them?
resulting text_cleaned_no_emoticons:  another perfect flight.   How come on your planes,  the sun visors can stay down?  Other carriers make you raise them?
resulting text_cleaned_no_emojis: Nice 
resulting text_cleaned_no_emoticons: Nice 
Unable to grab emoticons flag at row number: 465
Unable to grab emoticons value at row number: 465
resulting text_cleaned_no_emojis:  I love the dancing little richard. cool beans.
resulting text_cleaned_no_emoticons:  I love the dancing little richard. cool beans.
Unable to grab emoticons flag at row number: 466
Unable to grab emoticons value at row number: 466
resulting text_cleaned_no_emojis:  I don’t use Passbook =/ I still love you though <3 :) I’ll just use my email in the future.
resulting

resulting text_cleaned_no_emojis: .Thnx for the response  bot. It seems this 'improvement' could be easily attained. Is your 1st Class service really only worth $50?
resulting text_cleaned_no_emoticons: .Thnx for the response  bot. It seems this 'improvement' could be easily attained. Is your 1st Class service really only worth $50?
resulting text_cleaned_no_emojis:  has unrivalled access to #California with flights to the U.S. from 7 UK airports, with nonstop or one-stop connections year-round
resulting text_cleaned_no_emoticons:  has unrivalled access to #California with flights to the U.S. from 7 UK airports, with nonstop or one-stop connections year-round
Unable to grab emoticons flag at row number: 681
Unable to grab emoticons value at row number: 681
resulting text_cleaned_no_emojis:  booked award tix on ThaiAirways but I'm not seeing a conf# for them, just the United Flight Booking Problems#. Can you get get the Thai# for me?
resulting text_cleaned_no_emoticons:  booked award ti

...

resulting text_cleaned_no_emoticons:   see, James, we only have 7 dedicated inbound phone lines because telephones eat into our billions in profits
Unable to grab emoticons flag at row number: 14082
Unable to grab emoticons value at row number: 14082
resulting text_cleaned_no_emojis:   I did hear a last call for boarding of this flight when I was at JFK a few hours ago. good luck w/flights!
resulting text_cleaned_no_emoticons:   I did hear a last call for boarding of this flight when I was at JFK a few hours ago. good luck w/flights!
resulting text_cleaned_no_emojis:  , sitting on plane for 2.5hrs at gate due to computer sys issue, at what point do you Cancelled Flight a flight?, ridiculous 
resulting text_cleaned_no_emoticons:  , sitting on plane for 2.5hrs at gate due to computer sys issue, at what point do you Cancelled Flight a flight?, ridiculous 
resulting text_cleaned_no_emojis:   not a valid response in 2015 for a multinational corp whose profits are measured in billions. Stop 

Unable to grab emoticons flag at row number: 14204
Unable to grab emoticons value at row number: 14204
resulting text_cleaned_no_emojis:  It just hangs up and your agents on the ground are useless. How don't I have a seat on a first class ticket booked weeks ago?
resulting text_cleaned_no_emoticons:  It just hangs up and your agents on the ground are useless. How don't I have a seat on a first class ticket booked weeks ago?
resulting text_cleaned_no_emojis:  ive literally been holding for more than 2 HOURS now. i was told 2hrs. You all are sabotaging any chance i have of getting home
resulting text_cleaned_no_emoticons:  ive literally been holding for more than 2 HOURS now. i was told 2hrs. You all are sabotaging any chance i have of getting home
resulting text_cleaned_no_emojis:  we're still here guys - you are the worst
resulting text_cleaned_no_emoticons:  we're still here guys - you are the worst
resulting text_cleaned_no_emojis:  24 hours on the AirPort
resulting text_cleaned_no_e

resulting text_cleaned_no_emojis:  most horrendous service ever !! On off two planes. Been in Phil for 10 hrs. Now captain can't get flight info to print? #wtf
resulting text_cleaned_no_emoticons:  most horrendous service ever !! On off two planes. Been in Phil for 10 hrs. Now captain can't get flight info to print? #wtf
resulting text_cleaned_no_emojis:  you suck worst airline ever I will never be flying you again I have been stuck here for 13 hours no one is helping #fuckoff
resulting text_cleaned_no_emoticons:  you suck worst airline ever I will never be flying you again I have been stuck here for 13 hours no one is helping #fuckoff
resulting text_cleaned_no_emojis:  I have been on hold 3 hours.  2 seconds of it with a rude agent.
resulting text_cleaned_no_emoticons:  I have been on hold 3 hours.  2 seconds of it with a rude agent.
resulting text_cleaned_no_emojis:   Dear American, when did 2 hour hold times become the industry standard?  Have you heard of additional staffing during

Unable to grab emoticons flag at row number: 14517
Unable to grab emoticons value at row number: 14517
resulting text_cleaned_no_emojis:  nah u boofin u dont talk like any humans i know. Respond like u actually have a brain. And again i dont want customer relations
resulting text_cleaned_no_emoticons:  nah u boofin u dont talk like any humans i know. Respond like u actually have a brain. And again i dont want customer relations
resulting text_cleaned_no_emojis:  I have no transportation to and going to some other city and getting to NY sometime on Wed?! I'm sorry that's not gonna cut
resulting text_cleaned_no_emoticons:  I have no transportation to and going to some other city and getting to NY sometime on Wed?! I'm sorry that's not gonna cut
resulting text_cleaned_no_emojis:  because of you, I am doing the one thing I tried to avoid. Thank you for sending me to baggage claim.
resulting text_cleaned_no_emoticons:  because of you, I am doing the one thing I tried to avoid. Thank you for

resulting text_cleaned_no_emojis:  leaving over 20 minutes Late Flight. No warnings or communication until we were 15 minutes Late Flight. That's called shitty customer svc
resulting text_cleaned_no_emoticons:  leaving over 20 minutes Late Flight. No warnings or communication until we were 15 minutes Late Flight. That's called shitty customer svc
resulting text_cleaned_no_emojis:  Please bring American Airlines to #BlackBerry10
resulting text_cleaned_no_emoticons:  Please bring American Airlines to #BlackBerry10
resulting text_cleaned_no_emojis:  you have my money, you change my flight, and don't answer your phones! Any other suggestions so I can make my commitment??
resulting text_cleaned_no_emoticons:  you have my money, you change my flight, and don't answer your phones! Any other suggestions so I can make my commitment??
resulting text_cleaned_no_emojis:  we have 8 ppl so we need 2 know how many seats are on the next flight. Plz put us on standby for 4 people on the next flight?
re

In [31]:
#Sanity check: briefly check some examples where we know emojis and emoticons do exist
df_example1 = df_tweets.loc[df_tweets['tweet_id'] == 569198104806699008]
print(df_example1['emojis_flag'])
print(df_example1['emojis'])
print(df_example1['text'])
print(df_example1['text_cleaned'])
print(df_example1['text_cleaned_without_emojis_emoticons'])

238    True
Name: emojis_flag, dtype: object
238    [😂, 💗]
Name: emojis, dtype: object
238    @VirginAmerica hahaha 😂@VirginAmerica YOU GUYS ARE AMAZING. I LOVE YOU GUYS!!!💗
Name: text, dtype: object
238     hahaha 😂 YOU GUYS ARE AMAZING. I LOVE YOU GUYS!!!💗
Name: text_cleaned, dtype: object
238     hahaha  YOU GUYS ARE AMAZING. I LOVE YOU GUYS!!!
Name: text_cleaned_without_emojis_emoticons, dtype: object


In [32]:
#Sanity check: briefly check some examples where we know emojis and emoticons do exist
df_example1 = df_tweets.loc[df_tweets['tweet_id'] == 570270684619923457]
print(df_example1['emojis_flag'])
print(df_example1['emojis'])
print(df_example1['text'])
print(df_example1['text_cleaned'])
print(df_example1['text_cleaned_without_emojis_emoticons'])

18    True
Name: emojis_flag, dtype: object
18    [❤, ☺, 👍]
Name: emojis, dtype: object
18    I ❤️ flying @VirginAmerica. ☺️👍
Name: text, dtype: object
18    I ❤️ flying . ☺️👍
Name: text_cleaned, dtype: object
18    I ️ flying . ️
Name: text_cleaned_without_emojis_emoticons, dtype: object


In [33]:
#Sanity check: briefly check some examples where we know emojis and emoticons do exist
df_example2 = df_tweets.loc[df_tweets['tweet_id'] == 568890074164809728]
print(df_example2['emoticons_flag'])
print(df_example2['emoticons'])
print(df_example2['text'])
print(df_example2['text_cleaned'])
print(df_example2['text_cleaned_without_emojis_emoticons'])

277    True
Name: emoticons_flag, dtype: object
277    [:-)]
Name: emoticons, dtype: object
277    @VirginAmerica we have a hot female pilot! Sweet! DCA to SFO! :-)
Name: text, dtype: object
277     we have a hot female pilot! Sweet! DCA to SFO! :-)
Name: text_cleaned, dtype: object
277     we have a hot female pilot! Sweet! DCA to SFO! 
Name: text_cleaned_without_emojis_emoticons, dtype: object


### 8. Extract and Remove Hashtags
Some of the tweets have hashtag, which are keyword phrases spelled out with no spaces, and a pound sign at the front. They could offer more insight into the sentiment of the tweet. There were 3669 hashtags in the dataset in 2489 rows (some tweets evidently had more than one hashtag).

For now, the easiest approach would be to remove the hashtags and the words inside during text cleaning. If we have time, we can try to analyze the best approaches to extract the words from the hashtags, and split them into meaningful words. This would be fairly challenging, as some tweets have multiple words that are not capitalized, so there is not an easy, fool-proof way of extracing hashtags into words.

We also decided to extract the hashtags into a list inside a separate column for furtner analysis.

In [34]:
print(len(df_tweets.loc[df_tweets['text'].str.contains('#')]))

2489


In [35]:
#extracts hashtags into a list, which is put into a new column called 'hashtags', whilst also removing hashtags from the text_cleaned
def extract_and_remove_hashtags(df_tweets):
    regex_to_replace= r'#(\w+)'
    replace_value= ''
    df_tweets['hashtags'] = ''
    df_tweets['text_cleaned_without_emojis_emoticons_hashtags'] = ''
    
    for i, row in df_tweets.iterrows():    
        df_tweets.at[i, 'hashtags'] = re.findall(regex_to_replace, df_tweets.at[i, 'text_cleaned'])
        df_tweets.at[i, 'text_cleaned_without_emojis_emoticons_hashtags'] = re.sub(regex_to_replace, replace_value,  df_tweets.at[i, 'text_cleaned'])
        
    return df_tweets

In [36]:
df_tweets = extract_and_remove_hashtags(df_tweets)
df_tweets.loc[df_tweets['tweet_id'] == 569587242672398336]

tweet_id airline_sentiment  airline_sentiment_confidence  \
14637  569587242672398336           neutral                           1.0   

      negativereason  negativereason_confidence   airline  \
14637            NaN                        NaN  American   

                                                               text  \
14637  @AmericanAir Please bring American Airlines to #BlackBerry10   

                                           text_cleaned emojis_flag emojis  \
14637   Please bring American Airlines to #BlackBerry10       False     []   

      emoticons_flag emoticons  \
14637          False        []   

                  text_cleaned_without_emojis_emoticons        hashtags  \
14637   Please bring American Airlines to #BlackBerry10  [BlackBerry10]   

      text_cleaned_without_emojis_emoticons_hashtags  
14637             Please bring American Airlines to

### 9. Lowercase
Convert the text to lower case.

In [37]:
df_tweets['text_cleaned_lower_case'] = \
    df_tweets['text_cleaned_without_emojis_emoticons_hashtags'].apply(lambda text: text.lower())
df_tweets.head()

tweet_id airline_sentiment  airline_sentiment_confidence  \
0  570306133677760513           neutral                        1.0000   
1  570301130888122368          positive                        0.3486   
2  570301083672813571           neutral                        0.6837   
3  570301031407624196          negative                        1.0000   
4  570300817074462722          negative                        1.0000   

  negativereason  negativereason_confidence         airline  \
0            NaN                        NaN  Virgin America   
1            NaN                     0.0000  Virgin America   
2            NaN                        NaN  Virgin America   
3     Bad Flight                     0.7033  Virgin America   
4     Can't Tell                     1.0000  Virgin America   

                                                                                                                             text  \
0                                                                                             @VirginAmerica What @dhepburn said.   
1                                                        @VirginAmerica plus you've added commercials to the experience... tacky.   
2                                                         @VirginAmerica I didn't today... Must mean I need to take another trip!   
3  @VirginAmerica it's really aggressive to blast obnoxious "entertainment" in your guests' faces &amp; they have little recourse   
4                                                                         @VirginAmerica and it's a really big bad thing about it   

                                                                                                   text_cleaned  \
0                                                                                                   What  said.   
1                                                     plus you've added commercials to the experience... tacky.   
2                                                      I didn't today... Must mean I need to take another trip!   
3   it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse   
4                                                                      and it's a really big bad thing about it   

  emojis_flag emojis emoticons_flag emoticons  \
0       False     []          False        []   
1       False     []          False        []   
2       False     []          False        []   
3       False     []          False        []   
4       False     []          False        []   

                                                                          text_cleaned_without_emojis_emoticons  \
0                                                                                                   What  said.   
1                                                     plus you've added commercials to the experience... tacky.   
2                                                      I didn't today... Must mean I need to take another trip!   
3   it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse   
4                                                                      and it's a really big bad thing about it   

  hashtags  \
0       []   
1       []   
2       []   
3       []   
4       []   

                                                                 text_cleaned_without_emojis_emoticons_hashtags  \
0                                                                                                   What  said.   
1                                                     plus you've added commercials to the experience... tacky.   
2                                                      I didn't today... Must mean I need to take another trip!   
3   it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse   
4                                                          

### 10. Internet Slang abbreviations
We need to  so that they are the full words. We will use a dictionary of slang words, which we have used from here: 
https://github.com/Deffro/text-preprocessing-techniques/blob/master/slang.txt. We modified the dictionary to be in CSV format.

In [38]:
df_slang = pd.read_csv('..\data\slang.csv')
df_slang

slang_abbreviation                complete_form
0                 2day                        today
1                2nite                      tonight
2                   4u                      for you
3                4ward                      forward
4                   a3  anyplace, anywhere, anytime
..                 ...                          ...
285               yuge                         huge
286                 yw              you are welcome
287                ywa       you are welcome anyway
288               zomg                   oh my god!
289                zzz                     sleeping

[290 rows x 2 columns]

In [39]:
def replace_abbreviation(text, abbreviation, complete_form):
    return re.sub(abbreviation, complete_form, text)

In [40]:
#Sanity check, testing above function
regex_expression = re.compile('\\b'+'plz'+'\\b')
regex_to_replace =  'please'

replace_abbreviation(
    'o we fly straight into sfo and honululu gets pushed back 3.5 hours and now it looks like more delays.  i beg of you plz sort this out soon!',
    regex_expression,
    regex_to_replace
)



'o we fly straight into sfo and honululu gets pushed back 3.5 hours and now it looks like more delays.  i beg of you please sort this out soon!'

In [41]:
#Another sanity check, but a negative case this time around
#the word 'straight' should remain the same, even though the dictionary contains the abbreviation 'aight'
regex_expression = re.compile('\\b'+'aight'+'\\b')
regex_to_replace = 'alright'

replace_abbreviation(
    'o we fly straight into sfo and honululu gets pushed back 3.5 hours and now it looks like more delays.  i beg of you plz sort this out soon!',
    regex_expression,
    regex_to_replace
)

'o we fly straight into sfo and honululu gets pushed back 3.5 hours and now it looks like more delays.  i beg of you plz sort this out soon!'

In [42]:
#this function will find slang abbreviations and replace them with the complete forms
#needs df_tweets and df_slang
#returns a new dataframe with new column 'text_cleaned_without_emojis_emoticons_hashtags_abbreviations'

#we will iterate over every row/tweet and and see if there are instances of slang abbreviations
#computationally expensive, but because there are only 14000 rows, it's not too bad
#there is no easy way of detecting whether a word is an abbreviation or not using Spacy, NLTK, or spellchecker
def find_slang_abbreviations_and_replace_with_complete_form(df_tweets, df_slang):
    df_tweets['text_cleaned_no_abbreviations'] = ''
    
    for i, tweet_row in df_tweets.iterrows():
        df_tweets.at[i, 'text_cleaned_no_abbreviations'] = \
            df_tweets.at[i, 'text_cleaned_lower_case']
        
        if i % 1000 == 0:
            print('at row number: ' + str(i))
        
        for j, slang_row in df_slang.iterrows():
            #print(slang_row)
            slang_abbreviation = df_slang.at[j, 'slang_abbreviation'] 
            complete_form = df_slang.at[j, 'complete_form']
            
            #print("slang_abbreviation: " + slang_abbreviation)
            #print("complete_form: " + complete_form)
            
            regex_expression = re.compile('\\b'+slang_abbreviation+'\\b')
            regex_to_replace = complete_form
            
            df_tweets.at[i, 'text_cleaned_no_abbreviations'] = \
                replace_abbreviation(
                    df_tweets.at[i, 'text_cleaned_no_abbreviations'], 
                    regex_expression,
                    regex_to_replace
            )
            #print("current: " + df_tweets.at[i, 'text_cleaned_no_abbreviations'])

        
    return df_tweets

In [43]:
#create new column 'text_cleaned_no_abbreviations' in df_tweets
#by calling find_slang_abbreviations_and_replace_with_complete_form function
df_tweets = find_slang_abbreviations_and_replace_with_complete_form(df_tweets, df_slang)

at row number: 0
at row number: 1000
at row number: 2000
at row number: 3000
at row number: 4000
at row number: 5000
at row number: 6000
at row number: 7000
at row number: 8000
at row number: 9000
at row number: 10000
at row number: 11000
at row number: 12000
at row number: 13000
at row number: 14000


In [44]:
df_tweets.head()

tweet_id airline_sentiment  airline_sentiment_confidence  \
0  570306133677760513           neutral                        1.0000   
1  570301130888122368          positive                        0.3486   
2  570301083672813571           neutral                        0.6837   
3  570301031407624196          negative                        1.0000   
4  570300817074462722          negative                        1.0000   

  negativereason  negativereason_confidence         airline  \
0            NaN                        NaN  Virgin America   
1            NaN                     0.0000  Virgin America   
2            NaN                        NaN  Virgin America   
3     Bad Flight                     0.7033  Virgin America   
4     Can't Tell                     1.0000  Virgin America   

                                                                                                                             text  \
0                                                                                             @VirginAmerica What @dhepburn said.   
1                                                        @VirginAmerica plus you've added commercials to the experience... tacky.   
2                                                         @VirginAmerica I didn't today... Must mean I need to take another trip!   
3  @VirginAmerica it's really aggressive to blast obnoxious "entertainment" in your guests' faces &amp; they have little recourse   
4                                                                         @VirginAmerica and it's a really big bad thing about it   

                                                                                                   text_cleaned  \
0                                                                                                   What  said.   
1                                                     plus you've added commercials to the experience... tacky.   
2                                                      I didn't today... Must mean I need to take another trip!   
3   it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse   
4                                                                      and it's a really big bad thing about it   

  emojis_flag emojis emoticons_flag emoticons  \
0       False     []          False        []   
1       False     []          False        []   
2       False     []          False        []   
3       False     []          False        []   
4       False     []          False        []   

                                                                          text_cleaned_without_emojis_emoticons  \
0                                                                                                   What  said.   
1                                                     plus you've added commercials to the experience... tacky.   
2                                                      I didn't today... Must mean I need to take another trip!   
3   it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse   
4                                                                      and it's a really big bad thing about it   

  hashtags  \
0       []   
1       []   
2       []   
3       []   
4       []   

                                                                 text_cleaned_without_emojis_emoticons_hashtags  \
0                                                                                                   What  said.   
1                                                     plus you've added commercials to the experience... tacky.   
2                                                      I didn't today... Must mean I need to take another trip!   
3   it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse   
4                                                          

In [45]:
#sanity check
df_tweets.loc[df_tweets['tweet_id'] == 568899587424931840]

tweet_id airline_sentiment  airline_sentiment_confidence  \
2788  568899587424931840          negative                           1.0   

     negativereason  negativereason_confidence airline  \
2788    Late Flight                        1.0  United   

                                                                                                                                             text  \
2788  @united so we fly into SFO and Honululu gets pushed back 3.5 hours and now it looks like more delays.  I beg of you plz sort this out soon!   

                                                                                                                              text_cleaned  \
2788   so we fly into SFO and Honululu gets pushed back 3.5 hours and now it looks like more delays.  I beg of you plz sort this out soon!   

     emojis_flag emojis emoticons_flag emoticons  \
2788       False     []          False        []   

                                                                                                     text_cleaned_without_emojis_emoticons  \
2788   so we fly into SFO and Honululu gets pushed back 3.5 hours and now it looks like more delays.  I beg of you plz sort this out soon!   

     hashtags  \
2788       []   

                                                                                            text_cleaned_without_emojis_emoticons_hashtags  \
2788   so we fly into SFO and Honululu gets pushed back 3.5 hours and now it looks like more delays.  I beg of you plz sort this out soon!   

                                                                                                                   text_cleaned_lower_case  \
2788   so we fly into sfo and honululu gets pushed back 3.5 hours and now it looks like more delays.  i beg of you plz sort this out soon!   

                                                                                                                text_cleaned_no_abbreviations  
2788   so we fly into sfo and honululu gets pushed back 3.5 hours and now it looks like more delays.  i beg of you please sort this out soon!

### 11. Removing StopWords and Punctuation and numbers, and Lemmatization
We want to remove stop words because most common words such as "the", "and", "I", "you"  are not likely to add any value to our sentiment analysis. Removing stopwords will therefore reduce the noise that will reduce the effectiveness of our eventual sentiment analysis model. Removing stopwords is also beneficial in the sense that it also removes common contractions such as "I've, you're, etc."

We also want to remove punctuation because punctuation is not useful to our sentiment analysis. Punctutation might help determine the intensity, or polarity of text, but that is not relevant to sentiment. Similar to punctuation, we also want to remove numbers.

Lastly, we will need to perform lemmatization, so that we can reduce the  words to their root form

In [64]:
#load spacy model
import spacy

nlp = spacy.load('en_core_web_md')

In [65]:
df_tweets['text_list_no_stop_words'] = ''
df_tweets['lemmas_list'] = ''
    
for i, row in df_tweets.iterrows():   
    if i % 1000 == 0:
        print('at row number: ' + str(i))
    
    text = df_tweets.at[i, 'text_cleaned_no_abbreviations']
    
    #tokenize text into list of tokens
    token_list = nlp(text)
    
    text_list_no_stop_words = []
    lemmas_list = []
    
    #remove stop words, and lemmatize
    for token in token_list:
        #print(str(token.is_stop))
        #print(str(token.pos_))
        
        #if token is not a stop word, and not punctuation, and not a number, 
        #then it is useful to us and we store them in our lists        
        if (token.is_stop == False) & (token.pos_ != 'PUNCT') & (token.pos_ != 'NUM'):
            text_list_no_stop_words.append(token.text)
            lemmas_list.append(token.lemma_)
    
    #print('text_list_no_stop_words:' + str(text_list_no_stop_words))
    #print('lemmas_list:' + str(lemmas_list))
    df_tweets.at[i, 'text_list_no_stop_words'] = " ".join(text_list_no_stop_words)
    df_tweets.at[i, 'lemmas_list'] = " ".join(lemmas_list)

at row number: 0
at row number: 1000
at row number: 2000
at row number: 3000
at row number: 4000
at row number: 5000
at row number: 6000
at row number: 7000
at row number: 8000
at row number: 9000
at row number: 10000
at row number: 11000
at row number: 12000
at row number: 13000
at row number: 14000


In [66]:
#sanity check
df_tweets.head()

tweet_id airline_sentiment  airline_sentiment_confidence  \
0  570306133677760513           neutral                        1.0000   
1  570301130888122368          positive                        0.3486   
2  570301083672813571           neutral                        0.6837   
3  570301031407624196          negative                        1.0000   
4  570300817074462722          negative                        1.0000   

  negativereason  negativereason_confidence         airline  \
0            NaN                        NaN  Virgin America   
1            NaN                     0.0000  Virgin America   
2            NaN                        NaN  Virgin America   
3     Bad Flight                     0.7033  Virgin America   
4     Can't Tell                     1.0000  Virgin America   

                                                                                                                             text  \
0                                                                                             @VirginAmerica What @dhepburn said.   
1                                                        @VirginAmerica plus you've added commercials to the experience... tacky.   
2                                                         @VirginAmerica I didn't today... Must mean I need to take another trip!   
3  @VirginAmerica it's really aggressive to blast obnoxious "entertainment" in your guests' faces &amp; they have little recourse   
4                                                                         @VirginAmerica and it's a really big bad thing about it   

                                                                                                   text_cleaned  \
0                                                                                                   What  said.   
1                                                     plus you've added commercials to the experience... tacky.   
2                                                      I didn't today... Must mean I need to take another trip!   
3   it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse   
4                                                                      and it's a really big bad thing about it   

  emojis_flag emojis emoticons_flag emoticons  \
0       False     []          False        []   
1       False     []          False        []   
2       False     []          False        []   
3       False     []          False        []   
4       False     []          False        []   

                                                                          text_cleaned_without_emojis_emoticons  \
0                                                                                                   What  said.   
1                                                     plus you've added commercials to the experience... tacky.   
2                                                      I didn't today... Must mean I need to take another trip!   
3   it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse   
4                                                                      and it's a really big bad thing about it   

  hashtags  \
0       []   
1       []   
2       []   
3       []   
4       []   

                                                                 text_cleaned_without_emojis_emoticons_hashtags  \
0                                                                                                   What  said.   
1                                                     plus you've added commercials to the experience... tacky.   
2                                                      I didn't today... Must mean I need to take another trip!   
3   it's really aggressive to blast obnoxious "entertainment" in your guests' faces & they have little recourse   
4                                                          

Cleaning data is now complete, we'll save the dataframe to a csv. 

In [68]:
df_tweets.to_csv('..\data\Tweets_cleaned.csv', index = False)